In [5]:
import graphlab
graphlab.canvas.set_target('ipynb')

# Read some product review data

In [2]:
products = graphlab.SFrame('amazon_baby.gl')

[INFO] This non-commercial license of GraphLab Create is assigned to coursera@thomas.parisot.meand will expire on September 24, 2016. For commercial licensing options, visit https://dato.com/buy/.

[INFO] Start server at: ipc:///tmp/graphlab_server-40 - Server binary: /usr/local/lib/python2.7/site-packages/graphlab/unity_server - Server log: /tmp/graphlab_server_1444473140.log
[INFO] GraphLab Server Version: 1.6.1


In [9]:
products.head()

Columns:
	name	str
	review	str
	rating	float

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
|    Planetwise Flannel Wipes   | These flannel wipes are OK... |  3.0   |
|     Planetwise Wipe Pouch     | it came early and was not ... |  5.0   |
| Annas Dream Full Quilt wit... | Very soft and comfortable ... |  5.0   |
| Stop Pacifier Sucking with... | This is a product well wor... |  5.0   |
| Stop Pacifier Sucking with... | All of my kids have cried ... |  5.0   |
| Stop Pacifier Sucking with... | When the Binky Fairy came ... |  5.0   |
| A Tale of Baby's Days with... | Lovely book, it's bound ti... |  4.0   |
| Baby Tracker&reg; - Daily ... | Perfect for new parents. W... |  5.0   |
| Baby Tracker&reg; - Daily ... | A friend of mine pinned th... |  5.0   |
| Baby Tracker&reg; - Daily ... | This has been an easy way ... |  4.0   |
+-------------------------------+-------------------------------+--------+
[10 rows x 3 columns]

In [10]:
products.show()

# Build the vector word count

In [11]:
products['word_count'] = graphlab.text_analytics.count_words(products['review'])

In [12]:
products.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
|    Planetwise Flannel Wipes   | These flannel wipes are OK... |  3.0   |
|     Planetwise Wipe Pouch     | it came early and was not ... |  5.0   |
| Annas Dream Full Quilt wit... | Very soft and comfortable ... |  5.0   |
| Stop Pacifier Sucking with... | This is a product well wor... |  5.0   |
| Stop Pacifier Sucking with... | All of my kids have cried ... |  5.0   |
| Stop Pacifier Sucking with... | When the Binky Fairy came ... |  5.0   |
| A Tale of Baby's Days with... | Lovely book, it's bound ti... |  4.0   |
| Baby Tracker&reg; - Daily ... | Perfect for new parents. W... |  5.0   |
| Baby Tracker&reg; - Daily ... | A friend of mine pinned th... |  5.0   |
| Baby Tracker&reg; - Daily ... | This has been an easy way ... |  4.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+
|           word_count          |
+-------------------------------+
| {'and': 5, 'stink': 1, 'be... |
| {'and': 3, 'love': 1, 'it'... |
| {'and': 2, 'quilt': 1, 'it... |
| {'ingenious': 1, 'and': 3,... |
| {'and': 2, 'parents!!': 1,... |
| {'and': 2, 'cute': 1, 'hel... |
| {'shop': 1, 'be': 1, 'is':... |
| {'feeding,': 1, 'and': 2, ... |
| {'and': 1, 'help': 1, 'giv... |
| {'journal.': 1, 'all': 1, ... |
+-------------------------------+
[10 rows x 4 columns]

In [13]:
products['name'].show()

# Explore Vulli Sophie

In [35]:
girafe_reviews = products[products['name'] == 'Vulli Sophie the Giraffe Teether']

In [36]:
len(girafe_reviews)

785

In [22]:
girafe_reviews['rating'].show(view='Categorical')

# Build a sentiment classifier

In [24]:
products['rating'].show(view='Categorical')

## Define what is a positive and negative sentiment

In [25]:
# ignore 3 stars reviews
posneg_products = products[ products['rating'] != 3 ]

In [27]:
# positive sentiment is 4 or 5 stars
posneg_products['sentiment'] = posneg_products['rating'] >= 4

In [28]:
posneg_products.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	sentiment	int

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
|     Planetwise Wipe Pouch     | it came early and was not ... |  5.0   |
| Annas Dream Full Quilt wit... | Very soft and comfortable ... |  5.0   |
| Stop Pacifier Sucking with... | This is a product well wor... |  5.0   |
| Stop Pacifier Sucking with... | All of my kids have cried ... |  5.0   |
| Stop Pacifier Sucking with... | When the Binky Fairy came ... |  5.0   |
| A Tale of Baby's Days with... | Lovely book, it's bound ti... |  4.0   |
| Baby Tracker&reg; - Daily ... | Perfect for new parents. W... |  5.0   |
| Baby Tracker&reg; - Daily ... | A friend of mine pinned th... |  5.0   |
| Baby Tracker&reg; - Daily ... | This has been an easy way ... |  4.0   |
| Baby Tracker&reg; - Daily ... | I love this journal and ou... |  4.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+-----------+
|           word_count          | sentiment |
+-------------------------------+-----------+
| {'and': 3, 'love': 1, 'it'... |     1     |
| {'and': 2, 'quilt': 1, 'it... |     1     |
| {'ingenious': 1, 'and': 3,... |     1     |
| {'and': 2, 'parents!!': 1,... |     1     |
| {'and': 2, 'cute': 1, 'hel... |     1     |
| {'shop': 1, 'be': 1, 'is':... |     1     |
| {'feeding,': 1, 'and': 2, ... |     1     |
| {'and': 1, 'help': 1, 'giv... |     1     |
| {'journal.': 1, 'all': 1, ... |     1     |
| {'all': 1, 'forget': 1, 'j... |     1     |
+-------------------------------+-----------+
[10 rows x 5 columns]

## Let's train the sentiment classifier

In [29]:
train_data,test_data = posneg_products.random_split(.8, seed=0)

In [30]:
sentiment_model = graphlab.logistic_classifier.create(train_data, target='sentiment', features=['word_count'], validation_set=test_data)

PROGRESS: Logistic regression:
PROGRESS: --------------------------------------------------------
PROGRESS: Number of examples          : 133448
PROGRESS: Number of classes           : 2
PROGRESS: Number of feature columns   : 1
PROGRESS: Number of unpacked features : 219217
PROGRESS: Number of coefficients    : 219218
PROGRESS: Starting L-BFGS
PROGRESS: --------------------------------------------------------
PROGRESS: +-----------+----------+-----------+--------------+-------------------+---------------------+
PROGRESS: | Iteration | Passes   | Step size | Elapsed Time | Training-accuracy | Validation-accuracy |
PROGRESS: +-----------+----------+-----------+--------------+-------------------+---------------------+
PROGRESS: | 1         | 5        | 0.000002  | 3.818206     | 0.841481          | 0.839989            |
PROGRESS: | 2         | 9        | 3.000000  | 6.381193     | 0.947425          | 0.894877            |
PROGRESS: | 3         | 10       | 3.000000  | 7.294037     | 0.92

# Evaluate the sentiment model

In [31]:
sentiment_model.evaluate(test_data, metric='roc_curve')

{'roc_curve': Columns:
 	threshold	float
 	fpr	float
 	tpr	float
 	p	int
 	n	int
 
 Rows: 1001
 
 Data:
 +------------------+----------------+-----------------+-------+------+
 |    threshold     |      fpr       |       tpr       |   p   |  n   |
 +------------------+----------------+-----------------+-------+------+
 |       0.0        | 0.224474474474 | 0.0036102373463 | 27976 | 5328 |
 | 0.0010000000475  | 0.775525525526 |  0.996389762654 | 27976 | 5328 |
 | 0.00200000009499 | 0.735548048048 |  0.995353159851 | 27976 | 5328 |
 | 0.00300000002608 | 0.712837837838 |  0.99474549614  | 27976 | 5328 |
 | 0.00400000018999 | 0.69725975976  |  0.994280812125 | 27976 | 5328 |
 | 0.00499999988824 | 0.685998498498 |  0.993923362882 | 27976 | 5328 |
 | 0.00600000005215 | 0.676238738739 |  0.993422933943 | 27976 | 5328 |
 | 0.00700000021607 | 0.665728228228 |  0.993065484701 | 27976 | 5328 |
 | 0.00800000037998 | 0.655405405405 |  0.992815270232 | 27976 | 5328 |
 | 0.00899999961257 | 0.64808558

In [32]:
sentiment_model.show(view='Evaluation')

# Applying the learned model to understand sentiment

In [38]:
girafe_reviews['predicted_sentiment'] = sentiment_model.predict(girafe_reviews, output_type='probability')

In [39]:
girafe_reviews.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	predicted_sentiment	float

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
| Vulli Sophie the Giraffe T... | He likes chewing on all th... |  5.0   |
| Vulli Sophie the Giraffe T... | My son loves this toy and ... |  5.0   |
| Vulli Sophie the Giraffe T... | There really should be a l... |  1.0   |
| Vulli Sophie the Giraffe T... | All the moms in my moms' g... |  5.0   |
| Vulli Sophie the Giraffe T... | I was a little skeptical o... |  5.0   |
| Vulli Sophie the Giraffe T... | I have been reading about ... |  5.0   |
| Vulli Sophie the Giraffe T... | My neice loves her sophie ... |  5.0   |
| Vulli Sophie the Giraffe T... | What a friendly face!  And... |  5.0   |
| Vulli Sophie the Giraffe T... | We got this just for my so... |  5.0   |
| Vulli Sophie the Giraffe T... | My baby seems to like this... |  3.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+---------------------+
|           word_count          | predicted_sentiment |
+-------------------------------+---------------------+
| {'and': 1, 'all': 1, 'beca... |    0.999513023521   |
| {'and': 1, 'right': 1, 'he... |    0.999320678306   |
| {'and': 2, 'all': 1, 'late... |    0.013558811687   |
| {'and': 2, 'one!': 1, 'all... |    0.995769474148   |
| {'and': 3, 'all': 1, 'old'... |    0.662374415673   |
| {'and': 6, 'seven': 1, 'al... |    0.999997148186   |
| {'and': 4, 'drooling,': 1,... |    0.989190989536   |
| {'and': 3, 'chew': 1, "don... |    0.999563518413   |
| {'chew': 2, 'because': 1, ... |    0.970160542725   |
| {'and': 2, 'already': 1, '... |    0.195367644588   |
+-------------------------------+---------------------+
[10 rows x 5 columns]

In [41]:
girafe_reviews = girafe_reviews.sort('predicted_sentiment', ascending=False)

In [42]:
girafe_reviews.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	predicted_sentiment	float

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
| Vulli Sophie the Giraffe T... | Sophie, oh Sophie, your ti... |  5.0   |
| Vulli Sophie the Giraffe T... | I'm not sure why Sophie is... |  4.0   |
| Vulli Sophie the Giraffe T... | I'll be honest...I bought ... |  4.0   |
| Vulli Sophie the Giraffe T... | We got this little giraffe... |  5.0   |
| Vulli Sophie the Giraffe T... | As a mother of 16month old... |  5.0   |
| Vulli Sophie the Giraffe T... | Sophie the Giraffe is the ... |  5.0   |
| Vulli Sophie the Giraffe T... | Sophie la giraffe is absol... |  5.0   |
| Vulli Sophie the Giraffe T... | My 5-mos old son took to t... |  5.0   |
| Vulli Sophie the Giraffe T... | My nephews and my four kid... |  5.0   |
| Vulli Sophie the Giraffe T... | Never thought I'd see my s... |  5.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+---------------------+
|           word_count          | predicted_sentiment |
+-------------------------------+---------------------+
| {'giggles': 1, 'all': 1, "... |         1.0         |
| {'peace': 1, 'month': 1, '... |    0.999999999703   |
| {'all': 2, 'pops': 1, 'exi... |    0.999999999392   |
| {'all': 2, "don't": 1, '(l... |    0.99999999919    |
| {'cute': 1, 'all': 1, 'rev... |    0.999999998657   |
| {'just': 2, 'both': 1, 'mo... |    0.999999997108   |
| {'and': 5, 'the': 1, 'all'... |    0.999999995589   |
| {'just': 1, 'shape': 2, 'm... |    0.999999995573   |
| {'and': 4, 'chew': 1, 'all... |    0.999999989527   |
| {'giggles': 1, 'all': 1, '... |    0.999999985069   |
+-------------------------------+---------------------+
[10 rows x 5 columns]

In [44]:
girafe_reviews[0]['review']

"Sophie, oh Sophie, your time has come. My granddaughter, Violet is 5 months old and starting to teeth. What joy little Sophie brings to Violet. Sophie is made of a very pliable rubber that is sturdy but not tough. It is quite easy for Violet to twist Sophie into unheard of positions to get Sophie into her mouth. The little nose and hooves fit perfectly into small mouths, and the drooling has purpose. The paint on Sophie is food quality.Sophie was born in 1961 in France. The maker had wondered why there was nothing available for babies and made Sophie from the finest rubber, phthalate-free on St Sophie's Day, thus the name was born. Since that time millions of Sophie's populate the world. She is soft and for babies little hands easy to grasp. Violet especially loves the bumpy head and horns of Sophie. Sophie has a long neck that easy to grasp and twist. She has lovely, sizable spots that attract Violet's attention. Sophie has happy little squeaks that bring squeals of delight from Viol

In [45]:
girafe_reviews[1]['review']

"I'm not sure why Sophie is such a hit with the little ones, but my 7 month old baby girl is one of her adoring fans.  The rubber is softer and more pleasant to handle, and my daughter has enjoyed chewing on her legs and the nubs on her head even before she started teething.  She also loves the squeak that Sophie makes when you squeeze her.  Not sure what it is but if Sophie is amongst a pile of her other toys, my daughter will more often than not reach for Sophie.  And I have the peace of mind of knowing that only edible and safe paints and materials have been used to make Sophie, as opposed to Bright Starts and other baby toys made in China.  Now that the research is out on phthalates and other toxic substances in baby toys, I think it's more important than ever to find good quality toys that are also safe for our babies to handle and put in their mouths.  Sophie is a must-have for every new mom in my opinion.  Even if your kid is one of the few that can take or leave her, it's worth

In [46]:
girafe_reviews[-1]['review']

"My son (now 2.5) LOVED his Sophie, and I bought one for every baby shower I've gone to. Now, my daughter (6 months) just today nearly choked on it and I will never give it to her again. Had I not been within hearing range it could have been fatal. The strange sound she was making caught my attention and when I went to her and found the front curved leg shoved well down her throat and her face a purply/blue I panicked. I pulled it out and she vomited all over the carpet before screaming her head off. I can't believe how my opinion of this toy has changed from a must-have to a must-not-use. Please don't disregard any of the choking hazard comments, they are not over exaggerated!"

In [47]:
girafe_reviews[-2]['review']

"This children's toy is nostalgic and very cute. However, there is a distinct rubber smell and a very odd taste, yes I tried it, that my baby did not enjoy. Also, if it is soiled it is extremely difficult to clean as the rubber is a kind of porus material and does not clean well. The final thing is the squeaking device inside which stopped working after the first couple of days. I returned this item feeling I had overpaid for a toy that was defective and did not meet my expectations. Please do not be swayed by the cute packaging and hype surounding it as I was. One more thing, I was given a full refund from Amazon without any problem."

# Assignment

In [54]:
selected_words = ['awesome', 'great', 'fantastic', 'amazing', 'love', 'horrible', 'bad', 'terrible', 'awful', 'wow', 'hate']

In [56]:
products['word_count'] = graphlab.text_analytics.count_words(products['review'])

In [81]:
def fn (words):
    return dict((word,count) for word,count in words.iteritems() if word in selected_words)

products['filtered_word_count'] = products['word_count'].apply(fn)

In [99]:
products['filtered_word_count'].show(view='Dictionary')

In [103]:
# Question 1

# Most used: great
# Least used: wow

In [106]:
products = products[ products['rating'] != 3 ]
products['sentiment'] = products['rating'] >= 4

train_data,test_data = products.random_split(0.8, seed=0)
selected_words_model = graphlab.logistic_classifier.create(train_data, target='sentiment', features=['filtered_word_count'], validation_set=test_data)

PROGRESS: Logistic regression:
PROGRESS: --------------------------------------------------------
PROGRESS: Number of examples          : 133448
PROGRESS: Number of classes           : 2
PROGRESS: Number of feature columns   : 1
PROGRESS: Number of unpacked features : 11
PROGRESS: Number of coefficients    : 12
PROGRESS: Starting Newton Method
PROGRESS: --------------------------------------------------------
PROGRESS: +-----------+----------+--------------+-------------------+---------------------+
PROGRESS: | Iteration | Passes   | Elapsed Time | Training-accuracy | Validation-accuracy |
PROGRESS: +-----------+----------+--------------+-------------------+---------------------+
PROGRESS: | 1         | 2        | 0.315551     | 0.844299          | 0.842842            |
PROGRESS: | 2         | 3        | 0.532202     | 0.844186          | 0.842842            |
PROGRESS: | 3         | 4        | 0.749828     | 0.844276          | 0.843142            |
PROGRESS: | 4         | 5        | 

In [116]:
selected_words_model['coefficients'].sort('value', ascending=False)

Columns:
	name	str
	index	str
	class	int
	value	float

Rows: 12

Data:
+---------------------+-----------+-------+------------------+
|         name        |   index   | class |      value       |
+---------------------+-----------+-------+------------------+
| filtered_word_count |    love   |   1   |  1.39989834302   |
|     (intercept)     |    None   |   1   |  1.36728315229   |
| filtered_word_count |  awesome  |   1   |  1.05800888878   |
| filtered_word_count |  amazing  |   1   |  0.892802422508  |
| filtered_word_count | fantastic |   1   |  0.891303090304  |
| filtered_word_count |   great   |   1   |  0.883937894898  |
| filtered_word_count |    wow    |   1   | -0.0541450123332 |
| filtered_word_count |    bad    |   1   | -0.985827369929  |
| filtered_word_count |    hate   |   1   |  -1.40916406276  |
| filtered_word_count |   awful   |   1   |  -1.76469955631  |
+---------------------+-----------+-------+------------------+
[12 rows x 4 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.

In [117]:
selected_words_model['coefficients'].sort('value', ascending=False).print_rows(num_rows=15)

+---------------------+-----------+-------+------------------+
|         name        |   index   | class |      value       |
+---------------------+-----------+-------+------------------+
| filtered_word_count |    love   |   1   |  1.39989834302   |
|     (intercept)     |    None   |   1   |  1.36728315229   |
| filtered_word_count |  awesome  |   1   |  1.05800888878   |
| filtered_word_count |  amazing  |   1   |  0.892802422508  |
| filtered_word_count | fantastic |   1   |  0.891303090304  |
| filtered_word_count |   great   |   1   |  0.883937894898  |
| filtered_word_count |    wow    |   1   | -0.0541450123332 |
| filtered_word_count |    bad    |   1   | -0.985827369929  |
| filtered_word_count |    hate   |   1   |  -1.40916406276  |
| filtered_word_count |   awful   |   1   |  -1.76469955631  |
| filtered_word_count |  horrible |   1   |  -1.99651800559  |
| filtered_word_count |  terrible |   1   |  -2.09049998487  |
+---------------------+-----------+-------+------------

In [119]:
# higest weight: love (1.399)
# lowest weight: terrible (-2.0904)

In [120]:
selected_words_model.evaluate(test_data)

{'accuracy': 0.8431419649291376, 'confusion_matrix': Columns:
 	target_label	int
 	predicted_label	int
 	count	int
 
 Rows: 4
 
 Data:
 +--------------+-----------------+-------+
 | target_label | predicted_label | count |
 +--------------+-----------------+-------+
 |      0       |        0        |  234  |
 |      1       |        0        |  130  |
 |      0       |        1        |  5094 |
 |      1       |        1        | 27846 |
 +--------------+-----------------+-------+
 [4 rows x 3 columns]}

In [121]:
selected_words_model.show(view='Evaluation')

In [122]:
diaper_champ_reviews = products[ products['name'] == 'Baby Trend Diaper Champ' ]
len(diaper_champ_reviews)

298

In [123]:
diaper_champ_reviews['predicted_sentiment'] = sentiment_model.predict(diaper_champ_reviews, output_type='probability')

In [124]:
diaper_champ_reviews = diaper_champ_reviews.sort('predicted_sentiment', ascending=False)

In [125]:
diaper_champ_reviews.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	filtered_word_count	dict
	sentiment	int
	predicted_sentiment	float

Rows: 10

Data:
+-------------------------+-------------------------------+--------+
|           name          |             review            | rating |
+-------------------------+-------------------------------+--------+
| Baby Trend Diaper Champ | Baby Luke can turn a clean... |  5.0   |
| Baby Trend Diaper Champ | I LOOOVE this diaper pail!... |  5.0   |
| Baby Trend Diaper Champ | We researched all of the d... |  4.0   |
| Baby Trend Diaper Champ | My baby is now 8 months an... |  5.0   |
| Baby Trend Diaper Champ | This is absolutely, by far... |  5.0   |
| Baby Trend Diaper Champ | Diaper Champ or Diaper Gen... |  5.0   |
| Baby Trend Diaper Champ | Wow!  This is fabulous.  I... |  5.0   |
| Baby Trend Diaper Champ | I originally put this item... |  5.0   |
| Baby Trend Diaper Champ | Two girlfriends and two fa... |  5.0   |
| Baby Trend Diaper Champ | I am one of those super-cr... |  5.0   |
+-------------------------+-------------------------------+--------+
+-------------------------------+------------------------+-----------+
|           word_count          |  filtered_word_count   | sentiment |
+-------------------------------+------------------------+-----------+
| {'all': 1, 'less': 1, "fri... |           {}           |     1     |
| {'just': 1, 'over': 1, 'rw... |      {'love': 1}       |     1     |
| {'all': 2, 'just': 4, "don... |       {'bad': 1}       |     1     |
| {"don't": 1, 'when': 1, 'o... | {'bad': 1, 'great': 2} |     1     |
| {'just': 3, 'money': 1, 'n... |      {'love': 2}       |     1     |
| {'all': 1, 'bags.': 1, 'so... |           {}           |     1     |
| {'and': 4, '"genie".': 1, ... |           {}           |     1     |
| {'lysol': 1, 'all': 2, 'ba... |           {}           |     1     |
| {'just': 1, 'when': 1, 'bo... |    {'horrible': 1}     |     1     |
| {'taller': 1, 'bags.': 1, ... |      {'love': 1}       |     1     |
+-------------------------------+------------------------+-----------+
+---------------------+
| predicted_sentiment |
+---------------------+
|    0.999999937267   |
|    0.999999917406   |
|    0.999999899509   |
|    0.999999836182   |
|    0.999999824745   |
|    0.999999759315   |
|    0.999999692111   |
|    0.999999642488   |
|    0.999999604504   |
|    0.999999486804   |
+---------------------+
[10 rows x 7 columns]

In [126]:
# predicted sentiment for the most positive review
# 0.999999937267

In [127]:
selected_words_model.predict(diaper_champ_reviews[0:1], output_type='probability')

dtype: float
Rows: 1
[0.7969408512906698]

In [128]:
diaper_champ_reviews[0]['review']

'Baby Luke can turn a clean diaper to a dirty diaper in 3 seconds flat. The diaper champ turns the smelly diaper into "what diaper smell" in less time than that. I hesitated and wondered what I REALLY needed for the nursery. This is one of the best purchases we made. The champ, the baby bjorn, fluerville diaper bag, and graco pack and play bassinet all vie for the best baby purchase.Great product, easy to use, economical, effective, absolutly fabulous.UpdateI knew that I loved the champ, and useing the diaper genie at a friend\'s house REALLY reinforced that!! There is no comparison, the chanp is easy and smell free, the genie was difficult to use one handed (which is absolutly vital if you have a little one on a changing pad) and there was a deffinite odor eminating from the genieplus we found that the quick tie garbage bags where the ties are integrated into the bag work really well because there isn\'t any added bulk around the sealing edge of the champ.'

In [130]:
diaper_champ_reviews[0]['filtered_word_count']

{}

In [132]:
diaper_champ_reviews[1]['review']

'I LOOOVE this diaper pail!  Its the easiest to use!  after using the diaper genie for 2 months i decided i had enough with the refils and with how much of a pain it is to use.  I purchases this diaper pail in its place and i loooove it!  No more refills, it uses the same bags as my kitchen garbage!  And it holds alot more! I only have to empty it like once a week as oppsed to every other day with the diaper genie.  This is worth the few extra buck because you arnt spending 5 more bucks every othe rweek for refills!  I have a bunch of poopy diapers in mine and you cant even smell them! and i love the fact that you dont have to open it to put a diaper in so i can do it one handed.  Just toss the diaper in the top and flip over the handle, its sooo easy!  And with the diaper genie i noticed that the smell would leak out a bit when you opened the top.  It is a little bigger than the other pails, but it holds alot more!  I would definatly recommend this product to anyone looking to buy a d

In [134]:
diaper_champ_reviews[1]['filtered_word_count']

{'love': 1}